## Packages

In [10]:
import pandas as pd
from scipy import stats
import math
import yfinance as yf

## Import Data (2014-2023)

Data Source: CRSP

In [3]:
data_1 = pd.read_csv('data_1.csv')
data_2 = pd.read_csv('data_2.csv')
data_3 = pd.read_csv('data_3.csv')
data = pd.concat([data_1, data_2, data_3], ignore_index=True)

/var/folders/60/75vh_thj2m57nynzg5tgw0300000gn/T/ipykernel_86795/3829154129.py:1: DtypeWarning: Columns (7,8) have mixed types. Specify dtype option on import or set low_memory=False.
  data_1 = pd.read_csv('data_1.csv')
/var/folders/60/75vh_thj2m57nynzg5tgw0300000gn/T/ipykernel_86795/3829154129.py:2: DtypeWarning: Columns (7,8) have mixed types. Specify dtype option on import or set low_memory=False.
  data_2 = pd.read_csv('data_2.csv')
/var/folders/60/75vh_thj2m57nynzg5tgw0300000gn/T/ipykernel_86795/3829154129.py:3: DtypeWarning: Columns (7,8) have mixed types. Specify dtype option on import or set low_memory=False.
  data_3 = pd.read_csv('data_3.csv')


In [5]:
data.date = pd.to_datetime(data.date)
data

PERMNO       date TICKER        COMNAM  PERMCO        PRC  \
0         10158 2014-01-02   AMRC  AMERESCO INC   53454    9.78000   
1         10158 2014-01-03   AMRC  AMERESCO INC   53454    9.94000   
2         10158 2014-01-06   AMRC  AMERESCO INC   53454    9.74000   
3         10158 2014-01-07   AMRC  AMERESCO INC   53454    9.95000   
4         10158 2014-01-08   AMRC  AMERESCO INC   53454   10.12000   
...         ...        ...    ...           ...     ...        ...   
5715131   93436 2023-12-22   TSLA     TESLA INC   53453  252.53999   
5715132   93436 2023-12-26   TSLA     TESLA INC   53453  256.60999   
5715133   93436 2023-12-27   TSLA     TESLA INC   53453  261.44000   
5715134   93436 2023-12-28   TSLA     TESLA INC   53453  253.17999   
5715135   93436 2023-12-29   TSLA     TESLA INC   53453  248.48000   

                 VOL        RET       RETX  
0            73300.0   0.012422   0.012422  
1           105100.0   0.016360   0.016360  
2            76400.0  -0.020121  -0.020121  
3            86900.0   0.021561   0.021561  
4            79900.0   0.017085   0.017085  
...              ...        ...        ...  
5715131   93148541.0  -0.007701  -0.007701  
5715132   86700724.0   0.016116   0.016116  
5715133  106250779.0   0.018822   0.018822  
5715134  113250680.0  -0.031594  -0.031594  
5715135  100321201.0  -0.018564  -0.018564  

[5715136 rows x 9 columns]

## Russell 3000

Data Source: https://www.ishares.com/us/products/239714/ishares-russell-3000-etf

In [14]:
r3000 = pd.read_excel('Russell3000.xlsx', sheet_name='Holdings')
r3000

Ticker                             Name                  Sector  \
0        --             EMPIRE RESORT ESCROW  Consumer Discretionary   
1        --    ESC GCI LIBERTY INC SR ESCROW           Communication   
2        --   OMNIAB INC $15.00 VESTING Prvt             Health Care   
3        --   OMNIAB INC $12.50 VESTING Prvt             Health Care   
4         A         AGILENT TECHNOLOGIES INC             Health Care   
...     ...                              ...                     ...   
2678    ZUO                ZUORA INC CLASS A  Information Technology   
2679   ZVRA           ZEVRA THERAPEUTICS INC             Health Care   
2680    ZWS  ZURN ELKAY WATER SOLUTIONS CORP             Industrials   
2681   ZYME                    ZYMEWORKS INC             Health Care   
2682   ZYXI                        ZYNEX INC             Health Care   

     Asset Class  Market Value  Weight (%)  Notional Value  Quantity   Price  \
0         Equity          0.01     0.00000            0.01       881    0.00   
1         Equity          0.28     0.00000            0.28     28033    0.00   
2         Equity          0.02     0.00000            0.02      1502    0.00   
3         Equity          0.02     0.00000            0.02      1502    0.00   
4         Equity   10674454.32     0.06804     10674454.32     79494  134.28   
...          ...           ...         ...             ...       ...     ...   
2678      Equity     426402.90     0.00272       426402.90     43071    9.90   
2679      Equity     162158.50     0.00103       162158.50     18725    8.66   
2680      Equity    1548221.85     0.00987      1548221.85     39285   39.41   
2681      Equity     243538.71     0.00155       243538.71     14151   17.21   
2682      Equity      60373.38     0.00038        60373.38      7426    8.13   

           Location                      Exchange Currency  FX Rate  \
0     United States                        NASDAQ      USD        1   
1     United States                        NASDAQ      USD        1   
2     United States     NO MARKET (E.G. UNLISTED)      USD        1   
3     United States     NO MARKET (E.G. UNLISTED)      USD        1   
4     United States  New York Stock Exchange Inc.      USD        1   
...             ...                           ...      ...      ...   
2678  United States  New York Stock Exchange Inc.      USD        1   
2679  United States                        NASDAQ      USD        1   
2680  United States  New York Stock Exchange Inc.      USD        1   
2681  United States                        NASDAQ      USD        1   
2682  United States                        NASDAQ      USD        1   

     Accrual Date  
0              --  
1              --  
2              --  
3              --  
4              --  
...           ...  
2678           --  
2679           --  
2680           --  
2681           --  
2682           --  

[2683 rows x 14 columns]

## Cumulative Return (top 25% are winners and last 25% are losers, 2014-2023)

In [121]:
corr = {}

for year in range(2014, 2024):

    returns = {}
    print(year)
    
    for ticker in r3000.Ticker:
        
        if ticker == '--':
            continue

        else:
            sub_data = data[(data['TICKER']==ticker) & (data['date'].dt.year==year)]['RET']
        
            # Convert sub_data to float and drop NaN and 'C' values
            sub_data = sub_data[1:].dropna()
            sub_data = sub_data[sub_data != 'C']
            
            # Convert the remaining values to float
            sub_data = sub_data.astype(float)
            
            # Perform calculations or analysis on sub_data here
            if sub_data.empty:
                continue
            else:
                # Calculate cumulative return
                cumulative_return = (1 + sub_data).prod() - 1
                print(f"Ticker: {ticker}, Cumulative Return: {cumulative_return}")
                returns[ticker] = cumulative_return

    # Convert the dictionary to a sorted list of tuples (ticker, return)
    sorted_returns = sorted(returns.items(), key=lambda x: x[1], reverse=True)

    # Extract the top 25% and bottom 25%
    threshold = len(sorted_returns)//4
    top_25_ret = [ret for _, ret in sorted_returns[:threshold]]
    bottom_25_ret = [ret for _, ret in sorted_returns[-threshold:]]

    # Pearson Correlation Coefficient
    corr[year] = stats.pearsonr(top_25_ret, bottom_25_ret)

2014
Ticker: A, Cumulative Return: 0.01317442933737012
Ticker: AA, Cumulative Return: 1.2662476807829397
Ticker: AAL, Cumulative Return: 1.125463753613408
Ticker: AAOI, Cumulative Return: -0.2330853863329284
Ticker: AAON, Cumulative Return: 0.06861054252468257
Ticker: AAP, Cumulative Return: 0.45400936657409363
Ticker: AAPL, Cumulative Return: 0.4262334276659028
Ticker: AAT, Cumulative Return: 0.30621622402198634
Ticker: ABBV, Cumulative Return: 0.3001637297935664
Ticker: ABCB, Cumulative Return: 0.2353170674883065
Ticker: ABG, Cumulative Return: 0.40645000860857494
Ticker: ABM, Cumulative Return: 0.03767362254724871
Ticker: ABR, Cumulative Return: 0.08371384602367882
Ticker: ABT, Cumulative Return: 0.20394972042723758
Ticker: ACAD, Cumulative Return: 0.26243170158068874
Ticker: ACCO, Cumulative Return: 0.34679261186473953
Ticker: ACGL, Cumulative Return: 0.03016279848182668
Ticker: ACHC, Cumulative Return: 0.3009551321792938
Ticker: ACI, Cumulative Return: -0.6162841378404846
Ticker: 

### Historical correlation over the past 10 years

In [128]:
corr

{2014: PearsonRResult(statistic=0.46959216036849355, pvalue=2.9324431245008714e-24),
 2015: PearsonRResult(statistic=0.5986767913637976, pvalue=3.118769697453322e-44),
 2016: PearsonRResult(statistic=0.4392158675930635, pvalue=9.67956069583093e-23),
 2017: PearsonRResult(statistic=0.4675145245336921, pvalue=4.109686309079626e-27),
 2018: PearsonRResult(statistic=0.3377765582453998, pvalue=8.272198700337004e-15),
 2019: PearsonRResult(statistic=0.22828497653849453, pvalue=1.3056334776955425e-07),
 2020: PearsonRResult(statistic=0.41006281654474863, pvalue=6.3969335151151254e-24),
 2021: PearsonRResult(statistic=0.49773165457712193, pvalue=6.19352185140117e-40),
 2022: PearsonRResult(statistic=0.6519320729843044, pvalue=3.137731243597006e-78),
 2023: PearsonRResult(statistic=0.4220700097214984, pvalue=1.6542862090752028e-29)}

### Average correlation over the past 10 years

In [130]:
num = 0
count = 0

for year in range(2014, 2024):
    num += corr[year][0]
    count += 1

avg_corr = num/count
avg_corr

0.4522857432470614

### Correlation over the past 10 years

In [29]:
returns = {}

for ticker in r3000.Ticker:
    
    if ticker == '--':
        continue
    else:
        sub_data = data.loc[data['TICKER']==ticker, 'RET']
        
        # Convert sub_data to float and drop NaN and 'C' values
        sub_data = sub_data[1:].dropna()
        sub_data = sub_data[sub_data != 'C']
        
        # Convert the remaining values to float
        sub_data = sub_data.astype(float)
        
        # Perform calculations or analysis on sub_data here
        if sub_data.empty:
            print(f"No data found for ticker: {ticker}")
        else:
            # Calculate cumulative return
            cumulative_return = (1 + sub_data).prod() - 1
            print(f"Ticker: {ticker}, Cumulative Return: {cumulative_return}")
            returns[ticker] = cumulative_return

Ticker: A, Cumulative Return: 2.7182490370218457
Ticker: AA, Cumulative Return: 0.29676059122199816
Ticker: AAL, Cumulative Return: -0.42519528401016005
Ticker: AAOI, Cumulative Return: 0.3205742128797626
Ticker: AAON, Cumulative Return: 4.632926163361383
Ticker: AAP, Cumulative Return: -0.391738527414495
Ticker: AAPL, Cumulative Return: 10.116864135925649
Ticker: AAT, Cumulative Return: -0.006314122675347367
Ticker: ABBV, Cumulative Return: 3.4965792847864066
Ticker: ABCB, Cumulative Return: 1.8519630210896803
Ticker: ABG, Cumulative Return: 3.167730235365595
Ticker: ABM, Cumulative Return: 0.9274753286015445
Ticker: ABNB, Cumulative Return: -0.059210364546907646
Ticker: ABR, Cumulative Return: 4.742428965449019
Ticker: ABSI, Cumulative Return: -0.8054646538036427
Ticker: ABT, Cumulative Return: 2.4910699000064125
Ticker: ABUS, Cumulative Return: -0.7619038633515933
Ticker: ACA, Cumulative Return: 2.0692185711363473
Ticker: ACAD, Cumulative Return: 0.24492163327137018
Ticker: ACCD, Cu

In [34]:
# Convert the dictionary to a sorted list of tuples (ticker, return)
sorted_returns = sorted(returns.items(), key=lambda x: x[1], reverse=True)
sorted_returns

[('NVDA', 131.36658029797582),
 ('CHE', 64.50923988757485),
 ('AGM', 58.803621577246844),
 ('BHVN', 43.73069965544118),
 ('HEI', 41.20343514665843),
 ('CELH', 39.50484814842949),
 ('AMD', 36.31980864083767),
 ('WSO', 35.940441710198066),
 ('OLED', 32.597896947435856),
 ('MCO', 30.242449146577414),
 ('AVGO', 26.497396438016885),
 ('MATX', 25.587975880527882),
 ('USD', 25.234434400047334),
 ('TSLA', 23.831024397644608),
 ('TTD', 22.907034316222237),
 ('MDGL', 21.79637251602447),
 ('BLDR', 21.169780801793856),
 ('RDNT', 20.462763295091936),
 ('GLOB', 20.153754659356384),
 ('MPWR', 19.357461482974696),
 ('MGPI', 18.867451335281796),
 ('ENPH', 18.49041900182138),
 ('CDNS', 18.4407960476817),
 ('HUBS', 18.287550441826973),
 ('SAVA', 18.232986735977903),
 ('FICO', 17.964406803785092),
 ('STZ', 17.833359859280094),
 ('KNSL', 17.770178741683637),
 ('CECO', 17.730385388390758),
 ('LEN', 17.307542514528603),
 ('ANET', 16.127946780109465),
 ('COOP', 15.92335470349321),
 ('LRCX', 15.737429740992873

In [49]:
# Extract the top 25% and bottom 25%
n = len(sorted_returns)
top_25_ret = [ret for _, ret in sorted_returns[:n // 4]]
bottom_25_ret = [ret for _, ret in sorted_returns[-n // 4:]]

In [53]:
# Pearson Correlation Coefficient
corr = stats.pearsonr(top_25_ret, bottom_25_ret)
corr

PearsonRResult(statistic=0.5321633457929187, pvalue=4.237562105450146e-49)

## Sharpe Ratio (top 25% are winners and last 25% are losers, suppose annual risk-free rate is 3%, 2014-2023)

In [149]:
rf = 0.03/252
corr2 = {}

for year in range(2014, 2024):

    ratios = {}
    print(year)
    
    for ticker in r3000.Ticker:
        
        if ticker == '--':
            continue

        else:
            sub_data = data[(data['TICKER']==ticker) & (data['date'].dt.year==year)]['RET']
        
            # Convert sub_data to float and drop NaN and 'C' values
            sub_data = sub_data[1:].dropna()
            sub_data = sub_data[sub_data != 'C']
            
            # Convert the remaining values to float
            sub_data = sub_data.astype(float)
            
            # Perform calculations or analysis on sub_data here
            if sub_data.empty:
                continue
            else:
                
                # Calculate sharpe ratio
                std = sub_data.std()
                if std > 0:
                    sharpe_ratio = (sub_data.mean()-rf)/sub_data.std()
                else:
                    sharpe_ratio = 0
                
                print(f"Ticker: {ticker}, Sharpe Ratio: {sharpe_ratio}")

                # Make sure sharpe ratio is not nan or infinite
                if not math.isnan(sharpe_ratio) and sharpe_ratio != float('inf') and sharpe_ratio != float('-inf'):
                    ratios[ticker] = sharpe_ratio

    # Convert the dictionary to a sorted list of tuples (ticker, ratio)
    sorted_ratios = sorted(ratios.items(), key=lambda x: x[1], reverse=True)

    # Extract the top 25% and bottom 25%
    threshold = len(sorted_ratios)//4
    top_25_ratio = [ratio for _, ratio in sorted_ratios[:threshold]]
    bottom_25_ratio = [ratio for _, ratio in sorted_ratios[-threshold:]]

    # Pearson Correlation Coefficient
    corr2[year] = stats.pearsonr(top_25_ratio, bottom_25_ratio)

2014
Ticker: A, Sharpe Ratio: 0.00211449936034285
Ticker: AA, Sharpe Ratio: 0.08884911457636963
Ticker: AAL, Sharpe Ratio: 0.13083774664562675
Ticker: AAOI, Sharpe Ratio: -0.0058285325824522895
Ticker: AAON, Sharpe Ratio: 0.017299478829261382
Ticker: AAP, Sharpe Ratio: 0.09797035512059198
Ticker: AAPL, Sharpe Ratio: 0.10187899709287618
Ticker: AAT, Sharpe Ratio: 0.09967003813814859
Ticker: ABBV, Sharpe Ratio: 0.06740599427276964
Ticker: ABCB, Sharpe Ratio: 0.05986773395260155
Ticker: ABG, Sharpe Ratio: 0.07660087857716666
Ticker: ABM, Sharpe Ratio: 0.008332027372709537
Ticker: ABR, Sharpe Ratio: 0.023129227218932027
Ticker: ABT, Sharpe Ratio: 0.06871467827695062
Ticker: ACAD, Sharpe Ratio: 0.040900541765138985
Ticker: ACCO, Sharpe Ratio: 0.05912212267310779
Ticker: ACGL, Sharpe Ratio: 0.00347788031632955
Ticker: ACHC, Sharpe Ratio: 0.053665204451486904
Ticker: ACI, Sharpe Ratio: -0.0697714895453422
Ticker: ACIW, Sharpe Ratio: -0.010394129364707188
Ticker: ACLS, Sharpe Ratio: 0.01962047

### Historical correlation over the past 10 years

In [151]:
corr2

{2014: PearsonRResult(statistic=0.6017804106391679, pvalue=1.9586752545203714e-42),
 2015: PearsonRResult(statistic=0.19470524266319228, pvalue=3.84387342011429e-05),
 2016: PearsonRResult(statistic=0.4935187129125186, pvalue=4.008856384816433e-29),
 2017: PearsonRResult(statistic=0.3513343399747395, pvalue=3.2336745148143395e-15),
 2018: PearsonRResult(statistic=0.6557396259278835, pvalue=8.894523603770386e-63),
 2019: PearsonRResult(statistic=0.6911896177677278, pvalue=1.6279676357338472e-75),
 2020: PearsonRResult(statistic=0.2517007619442695, pvalue=1.816871029124191e-09),
 2021: PearsonRResult(statistic=0.5705440427423939, pvalue=1.4370814139738777e-54),
 2022: PearsonRResult(statistic=0.6014637124510219, pvalue=7.953435859466341e-64),
 2023: PearsonRResult(statistic=0.5439543570707451, pvalue=2.0825379756745828e-51)}

### Average correlation over the past 10 years

In [153]:
num = 0
count = 0

for year in range(2014, 2024):
    num += corr2[year][0]
    count += 1

avg_corr = num/count
avg_corr

0.49559308240936595

### Correlation Coefficient over the past 10 years

In [9]:
rf = 0.03/252
ratios2 = {}

for ticker in r3000.Ticker:
    
    if ticker == '--':
        continue
    else:
        sub_data = data.loc[data['TICKER']==ticker, 'RET']
        
        # Convert sub_data to float and drop NaN and 'C' values
        sub_data = sub_data[1:].dropna()
        sub_data = sub_data[sub_data != 'C']
        
        # Convert the remaining values to float
        sub_data = sub_data.astype(float)
        
        # Perform calculations or analysis on sub_data here
        if sub_data.empty:
            print(f"No data found for ticker: {ticker}")
        else:
            # Calculate sharpe ratio
            std = sub_data.std()
            if std > 0:
                sharpe_ratio = (sub_data.mean()-rf)/std
            else:
                sharpe_ratio = 0
                
            print(f"Ticker: {ticker}, Sharpe Ratio: {sharpe_ratio}")

            # Make sure sharpe ratio is not nan or infinite
            if not math.isnan(sharpe_ratio) and sharpe_ratio != float('inf') and sharpe_ratio != float('-inf'):
                ratios2[ticker] = sharpe_ratio

Ticker: A, Sharpe Ratio: 0.0327002749139943
Ticker: AA, Sharpe Ratio: 0.014373254517582217
Ticker: AAL, Sharpe Ratio: 0.004892529599923104
Ticker: AAOI, Sharpe Ratio: 0.02471923995524544
Ticker: AAON, Sharpe Ratio: 0.037223463595667514
Ticker: AAP, Sharpe Ratio: -0.0026957897614069168
Ticker: AAPL, Sharpe Ratio: 0.055873355564407284
Ticker: AAT, Sharpe Ratio: 0.0029864789410935628
Ticker: ABBV, Sharpe Ratio: 0.03692478645797407
Ticker: ABCB, Sharpe Ratio: 0.024477644891196665
Ticker: ABG, Sharpe Ratio: 0.03031970447159549
Ticker: ABM, Sharpe Ratio: 0.017149947749492113
Ticker: ABNB, Sharpe Ratio: 0.010730136913463436
Ticker: ABR, Sharpe Ratio: 0.03641966127257719
Ticker: ABSI, Sharpe Ratio: -0.013592506840566817
Ticker: ABT, Sharpe Ratio: 0.03303484208622701
Ticker: ABUS, Sharpe Ratio: 0.012371483729628319
Ticker: ACA, Sharpe Ratio: 0.04129026599790333
Ticker: ACAD, Sharpe Ratio: 0.019726982960973305
Ticker: ACCD, Sharpe Ratio: 0.0046379806154206605
Ticker: ACCO, Sharpe Ratio: 0.010013

In [11]:
sorted_ratios2 = sorted(ratios2.items(), key=lambda x: x[1], reverse=True)
sorted_ratios2

[('NGNE', 0.6382533009314276),
 ('BYON', 0.34537021183504785),
 ('TRML', 0.3177600876655866),
 ('SYRE', 0.2998770175987212),
 ('NLOP', 0.26788678131581223),
 ('CRGX', 0.25561585876371523),
 ('KRRO', 0.2516800672835723),
 ('WS', 0.21908001045955497),
 ('KNF', 0.1805842642713538),
 ('IRON', 0.13409300111135047),
 ('BIRK', 0.13272043370012848),
 ('VSTS', 0.13123628451158936),
 ('KGS', 0.11862560834533867),
 ('SKWD', 0.1177842436268444),
 ('WFRD', 0.10345318866470285),
 ('DRS', 0.10227006513133932),
 ('CXT', 0.09828367357016822),
 ('MBC', 0.0980775330219736),
 ('OABI', 0.09293137477325575),
 ('BCAL', 0.08597712330220414),
 ('VTS', 0.08593379680784374),
 ('CLMB', 0.08436038054891014),
 ('SEZL', 0.07886009764547476),
 ('CEG', 0.07818577282231406),
 ('NVDA', 0.07693102730173865),
 ('ASO', 0.07692689436523083),
 ('CHRD', 0.0747643266024058),
 ('APGE', 0.07408902332069206),
 ('PKST', 0.07337251783865985),
 ('ACLX', 0.07321641412775257),
 ('ESAB', 0.07262189543919377),
 ('KNSL', 0.07239187162917

In [13]:
# Extract the top 25% and bottom 25%
n = len(sorted_ratios2)
top_25_ratio = [ratio for _, ratio in sorted_ratios2[:n // 4]]
bottom_25_ratio = [ratio for _, ratio in sorted_ratios2[-n // 4:]]

In [15]:
# Pearson Correlation Coefficient
corr = stats.pearsonr(top_25_ratio, bottom_25_ratio)
corr

PearsonRResult(statistic=0.2259128608833849, pvalue=5.157692123549246e-09)

## Cumulative Return (top 25% are winners and last 25% are losers, 2024)

2024 Data Source: yahoo finance api

In [56]:
ret2024 = {}

for ticker in r3000.Ticker:
    
    if ticker == '--':
        continue
    else:
        comp = yf.Ticker(ticker)
        comp_data = comp.history(period='1y')
        
        if comp_data.empty:
            continue
        else:
            filter_data = comp_data.loc[comp_data.index.year==2024, 'Close']
            ret = filter_data.pct_change()
            cumulative_return = (1+ret[1:]).prod()-1
            ret2024[ticker] = cumulative_return

/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIn

ADRO: No data found, symbol may be delisted
ADRO: No data found, symbol may be delisted


/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIn

BFA: No data found, symbol may be delisted


/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')


...

/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIn

UHALB: No data found, symbol may be delisted


/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIn

XTSLA: No data found, symbol may be delisted


/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIn

In [60]:
sorted_ret2024 = sorted(ret2024.items(), key=lambda x:x[1], reverse=True)
sorted_ret2024

[('WGS', 24.92045363106512),
 ('SEZL', 16.990654526303278),
 ('LENZ', 8.258201500384128),
 ('ROOT', 7.4918816995733035),
 ('APP', 6.506188898935503),
 ('SMR', 6.328025305777509),
 ('SMMT', 5.935605582715313),
 ('ASTS', 3.9958762925113724),
 ('MSTR', 3.9719039178441786),
 ('CVNA', 3.931450895587435),
 ('INOD', 3.7175866726523283),
 ('RNA', 3.604803603473048),
 ('CORZ', 3.6017440873233006),
 ('LUMN', 3.518518532534892),
 ('JANX', 3.4246820595348915),
 ('ADMA', 3.184615410412153),
 ('WLFC', 3.1335004033919054),
 ('PLTR', 2.9668273188004437),
 ('VST', 2.765481323545009),
 ('CAPR', 2.6347658254526394),
 ('RKLB', 2.5781544641701775),
 ('FTAI', 2.543505960616448),
 ('CAVA', 2.4592612815684376),
 ('PRAX', 2.4334929878470852),
 ('IESC', 2.331869587799899),
 ('HROW', 2.264435058089945),
 ('PPTA', 2.231707461563913),
 ('REAX', 2.2142856700522167),
 ('NN', 2.1600000593397333),
 ('WULF', 2.121739120519456),
 ('POWL', 2.098665385581679),
 ('USLM', 2.0770552323483957),
 ('TPC', 2.0674778384127546),
 

In [66]:
# Extract the top 25% and bottom 25%
thres = len(sorted_ret2024)//4
top_25_ret = [ret for _, ret in sorted_ret2024[:thres]]
bottom_25_ret = [ret for _, ret in sorted_ret2024[-thres:]]

In [68]:
# Pearson Correlation Coefficient
corr = stats.pearsonr(top_25_ret, bottom_25_ret)
corr

PearsonRResult(statistic=0.3519154199871498, pvalue=8.605554835875287e-21)

## Sharpe Ratio (top 25% are winners and last 25% are losers, suppose annual risk-free rate is 3%, 2024)

In [73]:
ratio2024 = {}
rf = 0.03/252

for ticker in r3000.Ticker:
    
    if ticker == '--':
        continue
    else:
        comp = yf.Ticker(ticker)
        comp_data = comp.history(period='1y')
        
        if comp_data.empty:
            continue
        else:
            filter_data = comp_data.loc[comp_data.index.year==2024, 'Close']
            ret = filter_data.pct_change()
            
            std = ret.std()
            if std > 0:
                sharpe_ratio = (ret.mean()-rf)/std
            else:
                sharpe_ratio = 0
            
            # Make sure sharpe ratio is not nan or infinite
            if not math.isnan(sharpe_ratio) and sharpe_ratio != float('inf') and sharpe_ratio != float('-inf'):
                ratio2024[ticker] = sharpe_ratio

/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIn

ADRO: No data found, symbol may be delisted
ADRO: No data found, symbol may be delisted


/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIn

BFA: No data found, symbol may be delisted


/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')


...

/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIn

UHALB: No data found, symbol may be delisted


/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIn

XTSLA: No data found, symbol may be delisted


/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
/Users/anthony_ning/opt/anaconda3/lib/python3.9/site-packages/yfinance/utils.py:681: FutureWarning: The 'unit' keyword in TimedeltaIn

In [75]:
sorted_ratio2024 = sorted(ratio2024.items(), key=lambda x:x[1], reverse=True)
sorted_ratio2024

[('TRGP', 0.26596885991994423),
 ('DTM', 0.2508599460929475),
 ('SFM', 0.23378768763711394),
 ('AHR', 0.23161179837591855),
 ('FTAI', 0.22343899720704571),
 ('ECG', 0.21844654879449985),
 ('WGS', 0.21119397449117058),
 ('IBKR', 0.20730416502239218),
 ('USLM', 0.2059393645294975),
 ('WLFC', 0.2046530061662662),
 ('APP', 0.20409425241439405),
 ('EME', 0.19660274269505013),
 ('GVA', 0.19425690863960898),
 ('TPB', 0.1931573620000649),
 ('WMT', 0.19028092881910671),
 ('CNK', 0.18894363334992798),
 ('WMB', 0.18771030608059652),
 ('EAT', 0.187381446559052),
 ('FI', 0.18725011021199992),
 ('KMI', 0.18603584004377535),
 ('CAVA', 0.1850110133596683),
 ('GEV', 0.18350369798432067),
 ('VST', 0.18317578338907692),
 ('MSI', 0.18311651515627522),
 ('ALSN', 0.18187688415173617),
 ('SPOT', 0.17866805761159832),
 ('GDDY', 0.17802280701258574),
 ('TPL', 0.1741134595624468),
 ('BRO', 0.17362707691463616),
 ('UNM', 0.17331428736045),
 ('OKE', 0.17327188666176987),
 ('JEF', 0.17252985935088613),
 ('BSX', 0.

In [77]:
# Extract the top 25% and bottom 25%
thres = len(sorted_ratio2024)//4
top_25_ratio = [ratio for _, ratio in sorted_ratio2024[:thres]]
bottom_25_ratio = [ratio for _, ratio in sorted_ratio2024[-thres:]]

In [79]:
# Pearson Correlation Coefficient
corr = stats.pearsonr(top_25_ratio, bottom_25_ratio)
corr

PearsonRResult(statistic=0.8016228214215948, pvalue=4.8029953805858064e-150)

## Reference

In [28]:
tickers = ''

for ticker in r3000.Ticker[1800:]:
    
    if ticker == '--':
        continue
    else:
        tickers += ticker
        tickers += ' '
        
tickers = tickers.rstrip()
tickers

'OPRX ORA ORC ORCL ORGO ORI ORIC ORLY ORRF OSBC OSCR OSIS OSK OSPN OSUR OSW OTIS OTLK OTTR OUST OUT OVV OWL OXM OXY OZK P5N994 PACB PACK PACS PAG PAGS PAHC PANL PANW PAR PARA PARAA PARR PATH PATK PAX PAYC PAYO PAYS PAYX PB PBF PBH PBPB PCAR PCG PCH PCOR PCRX PCT PCTY PCVX PD PDCO PDFS PDM PEB PEBO PECO PEG PEGA PEN PENG PENN PEP PEPG PFBC PFC PFE PFG PFGC PFIS PFMT PFS PFSI PG PGC PGEN PGNY PGR PGRE PGY PH PHAT PHIN PHM PHR PI PII PINC PINS PIPR PJT PK PKE PKG PKST PL PLAB PLAY PLD PLL PLMR PLNT PLOW PLPC PLRX PLSE PLTK PLTR PLUG PLUS PLXS PLYM PM PMT PNC PNFP PNR PNTG PNW PODD POOL POR POST POWI POWL POWW PPBI PPC PPG PPL PPTA PR PRA PRAA PRAX PRCT PRDO PRG PRGO PRGS PRI PRIM PRK PRKS PRLB PRM PRMB PRME PRO PROK PRTA PRU PRVA PSA PSFE PSMT PSN PSTG PSTL PSX PTC PTCT PTEN PTGX PTLO PTON PTVE PUBM PUMP PVH PWP PWR PX PYCR PYPL PZZA QCOM QCRH QDEL QGEN QLYS QNST QRVO QS QSI QTRX QTTB QTWO R RAMP RAPT RARE RBA RBB RBBN RBC RBCAA RBLX RC RCEL RCKT RCL RCM RCUS RDFN RDN RDNT RDUS RDVT REAX 